# choose OS

In [104]:
home_dir = "/home/e.sharaborin/"
# home_dir = "/Users/weugene/"
a4width = 2480
a4height = 3508
figborderlinesize = 0.7
legborderlinesize = 0.7

In [109]:
import matplotlib.pyplot as plt
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.io as pio
import os
import numpy as np
# import math
# from math import floor, log10
from numpy import floor, log10

init_notebook_mode(connected=True)
import csv
title="Mass Conservation vs time"
xlabel="t"
ylabel="V"

# MYPATH="/Users/weugene/Dropbox/Aslan-Evgenii/media/pictures/"
MYPATH = home_dir + "/Dropbox/Aslan-Evgenii/media/pictures/"

basename= home_dir + "/basilisk/work/Verification_ring/"
# rpath = 'C:/Users/Weugene/AppData/Local/Packages/CanonicalGroupLimited.UbuntuonWindows_79rhkp1fndgsc/LocalState/rootfs/home/e.sharaborin/basilisk/work/tube/'
rpath = home_dir + '/basilisk/work/Verification_ring/'

# prefix = "Mass conservation"
prefix = "Moving solid"
names=["BPM", "SSM"]
filenames = ["BPcons.txt", "Popinetcons.txt"]
lines = {}
xmin =[]; xmax=[]; ymin=[]; ymax=[]
for name,filename  in zip(names, filenames):
    try:
        with open(basename + filename, 'r')  as f_obj:
            x, y = zip(*[map(float, l.split()) for l in f_obj])
            x = np.asarray(x)
            y = np.asarray(y)
            lines[name] = {"x":x, "y":y}
            xmin.append(x.min());ymin.append(y.min());xmax.append(x.max());ymax.append(y.max());
    except FileNotFoundError:
        raise FileNotFoundError
xmin=min(xmin); xmax=max(xmax); ymin=min(ymin); ymax=max(ymax)
axis=[0,1.5, ymin, ymax*1.1]

yaxis = dict(
              tickfont = dict(
              family = 'Times New Roman',
              size = 20,
              color = 'black'
              ),
              titlefont = dict(
                  family = 'Times New Roman',
                  size = 25,
                  color = 'black'
              ),
          )
xaxis = dict(
              tickfont = dict(
                  family = 'Times New Roman',
                  size = 20,
                  color = 'black'
              ),
              titlefont = dict(
                  family = 'Times New Roman',
                  size = 25,
                  color = 'black'
              )
          )
axis_style = dict(showline=True, gridwidth=1, gridcolor='lightgrey', linewidth=figborderlinesize, linecolor='black', mirror=True, ticks='outside',
                 tickfont = dict(family = 'Times New Roman', size = 20, color = 'black'))
bg_style = {'plot_bgcolor': 'rgba(0, 0, 0, 0)', 'paper_bgcolor': 'rgba(0, 0, 0, 0)',}

# Define function for string formatting of scientific notation
def sci_notation(num, decimal_digits=1, precision=None, exponent=None):
    """
    Returns a string representation of the scientific
    notation of the given number formatted for use with
    LaTeX or Mathtext, with specified number of significant
    decimal digits and precision (number of decimal digits
    to show). The exponent to be used can also be specified
    explicitly.
    """
    if exponent is None:
        exponent = int(floor(log10(abs(num))))
    coeff = round(num / float(10**exponent), decimal_digits)
    if precision is None:
        precision = decimal_digits
    
    if abs(coeff - 1) < 1e-4:
        return r"10<sup>{}<sup>".format(exponent)
    return r"{}\u00B7 10<sup>{}</sup>".format(coeff, exponent)


No_margin_scheme = dict(
    autosize=False,
    width=800,
    height=400,
    margin=dict(
        l=0,
        r=0,
        b=0.,
        t=0,
        pad=0
    )
#     paper_bgcolor="LightSteelBlue",
)

In [110]:
import plotly.graph_objects as go
import numpy as np

fig = go.Figure()
for name in names:
    fig.add_trace(go.Scatter(x=lines[name]["x"], y=lines[name]["y"], mode='lines', name=name))
fig.update_layout(xaxis_title=xlabel,
                  yaxis_title=ylabel,
                  yaxis = yaxis,
                  xaxis = xaxis)
fig.update_xaxes(axis_style)
fig.update_yaxes(axis_style)

fig.update_layout(bg_style) 
fig.update_layout(legend = dict(font = dict(family = "Times New Roman", size = 20, color = "black")),
                  legend_title = dict(font = dict(family = "Times New Roman", size = 20, color = "blue")))

fig.update_layout(legend=dict(
    yanchor="top",
    y=0.8,
    xanchor="right",
    x=0.99,
    bgcolor="White",
    bordercolor="Black",
    borderwidth=legborderlinesize
))
fig.update_layout(dict(
    autosize=False,
    width=600,
    height=300,
    margin=dict(
        l=0,
        b=0.,
        t=0,
        pad=0
    )
#     paper_bgcolor="LightSteelBlue",
))
iplot(fig)
pio.write_image(fig, MYPATH + prefix + '/mass_cons.pdf')

In [97]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
from plotly.offline import iplot, init_notebook_mode
import plotly.io as pio
import glob, os, sys
import logging
from sys import argv
import re
import csv
from scipy.signal import find_peaks
from pathlib import Path
# pio.orca.config.executable = str(Path('C:/Users/Weugene/AppData/Local/Programs/orca/orca.exe'))
np.set_printoptions(threshold=sys.maxsize)
import scipy.spatial.distance as ds

# prefix = 'C:/Users/Weugene/AppData/Local/Packages/CanonicalGroupLimited.UbuntuonWindows_79rhkp1fndgsc/LocalState/rootfs'
prefix = ''
rpath = prefix + '/home/e.sharaborin/basilisk/work/mass_conservation/COMPARISON/'
files_csv = ['m0.08',  'm0.125',  'm0.2']
names = ['r<sub>1</sub>=0.08', 'r<sub>1</sub>=0.125', 'r<sub>1</sub>=0.2' ]
ynames = ['V<sub>g</sub>', 'U<sub>mean</sub>', 'U<sub>max</sub>']
fnames = ['Vg', 'Umean', 'Umax']
lines = ['solid', 'dot', 'dash', 'longdash']
print ("path:", rpath)

#WINDOWS 10
path_ex = rpath
#MAC OS
# path_ex = '/Users/weugene/basilisk/work/tube/'
for i,f in enumerate(files_csv):
    files_csv[i] = rpath + files_csv[i]
### STYLE
yaxis = dict(
              tickfont = dict(
              family = 'Times New Roman',
              size = 20,
              color = 'black'
              ),
              titlefont = dict(
                  family = 'Times New Roman',
                  size = 25,
                  color = 'black'
              ),
          )
xaxis = dict(
              tickfont = dict(
                  family = 'Times New Roman',
                  size = 20,
                  color = 'black'
              ),
              titlefont = dict(
                  family = 'Times New Roman',
                  size = 25,
                  color = 'black'
              )
          )
# axis_style = dict(showline=True, gridwidth=1, gridcolor='lightgrey', linewidth=2, linecolor='black', mirror=True, ticks='outside',
#                  tickfont = dict(family = 'Times New Roman', size = 18, color = 'black'))
# bg_style = {'plot_bgcolor': 'rgba(255, 255, 255, 1)', 'paper_bgcolor': 'rgba(255, 255, 255, 1)',}
col =   ['blue',           'red',        'hsv(120,100,100)',       'black' ]

### END of STYLE


headers1=['level', 'i', 't', 'dt','avggas','statuavg', 'staturms', 'statumax', 'MY_NAN' ]

df_exp = []

for i, file in enumerate(files_csv):
    print('FILE name: ',file)
    df_exp.append(pd.read_csv(Path(file), header=None, sep=' '))
    df_exp[i].columns = headers1
    
for j,y in enumerate(['avggas', 'statuavg', 'statumax']):
    fig = go.Figure()
    for i, file in enumerate(files_csv):
#         print(y)
#         print(df_exp[i]['t'])
#         print(df_exp[i][y])
        if y =='avggas':
            df_exp[i][y] -= df_exp[i]['avggas'][0]
        fig.add_trace(go.Scatter(x=df_exp[i]['t'], y=df_exp[i][y], name=names[i],
                             mode='lines+markers',
                             line=dict(color=col[i], width=2, dash = lines[i]),
                             textfont=dict(
                                family="Times New Roman",
                                size=18,
                                color="LightSeaGreen")
                             ))

    fig.update_layout(
        width = 1000,
        height = 500,
        xaxis_title='t',
        yaxis_title=ynames[j],
        yaxis = yaxis,
        xaxis = xaxis
    )
    fig.update_layout(bg_style)
    fig.update_xaxes(axis_style)
    fig.update_yaxes(axis_style)
    # fig.update_layout( yaxis_type = "log" )
    maxy = max(df_exp[0][y])
    if y == 'statumax':
        maxy = 200
#     fig.update_yaxes(range=[0,0.39])
    fig.update_xaxes(range=[0,0.39])
    fig.update_layout(showlegend=True)
    fig.update_layout(legend = dict(font = dict(family = "Times New Roman", size = 25, color = "black")),
                      legend_title = dict(font = dict(family = "Times New Roman", size = 25, color = "blue")))

    fig.update_layout(legend=dict(
        yanchor="bottom",
        y=0.1,
        xanchor="right",
        x=1,
        bgcolor="White",
        bordercolor="Black",
        borderwidth=figborderlinesize
    ))
    fig.update_layout(
        autosize=False,
        width=850,
        height=600,
        margin=dict(
            l=1,
            r=1,
            b=1,
            t=1,
            pad=4
        ),
    #     paper_bgcolor="LightSteelBlue",
    )

    if True:
        fn = rpath + fnames[j] + '.pdf'
        iplot(fig)
        pio.write_image(fig, str(Path(fn)))
        print("Successfully generated:", fn)


path: /home/e.sharaborin/basilisk/work/mass_conservation/COMPARISON/
FILE name:  /home/e.sharaborin/basilisk/work/mass_conservation/COMPARISON/m0.08
FILE name:  /home/e.sharaborin/basilisk/work/mass_conservation/COMPARISON/m0.125
FILE name:  /home/e.sharaborin/basilisk/work/mass_conservation/COMPARISON/m0.2


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/COMPARISON/Vg.pdf


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/COMPARISON/Umean.pdf


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/COMPARISON/Umax.pdf


# Convergence test all in one

In [117]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
from plotly.offline import iplot, init_notebook_mode
import plotly.io as pio
import glob, os, sys
import logging
from sys import argv
import re
import csv
from scipy.signal import find_peaks
from pathlib import Path
import os.path

# pio.orca.config.executable = str(Path('C:/Users/Weugene/AppData/Local/Programs/orca/orca.exe'))
np.set_printoptions(threshold=sys.maxsize)
import scipy.spatial.distance as ds

# prefix = 'C:/Users/Weugene/AppData/Local/Packages/CanonicalGroupLimited.UbuntuonWindows_79rhkp1fndgsc/LocalState/rootfs'
prefix = ''
rpath = prefix + '/home/e.sharaborin/basilisk/work/mass_conservation/logs/'

files_csv = []
names = []
params = []
# for r in [0.2]:
#     for lev in [7, 8, 9]:
#         for tol in ['1e-6','1e-8']:
for ir, r in enumerate([0.05, 0.1, 0.2]):
    for jlev, lev in enumerate([7, 8, 9, 10]):
        for ktol, tol in enumerate(['1e-8']):
            file = rpath + 'log_r_{}_l_{}_t_{}'.format(r, lev, tol)
            if os.path.isfile(file) and os.path.getsize(file) > 0:
                files_csv.append(file)
                params.append({'r': r, 'lev': lev, 'tol': tol, 'ir': ir, 'jlev': jlev, 'ktol':ktol})
#                 names.append('r<sub>1</sub>={}, J<sub>max</sub>={}, \u025B<sub>P</sub>={}'.format(r, lev, tol))
                names.append('r<sub>1</sub>={}, J<sub>max</sub>={}'.format(r, lev))
fl = files_csv[:]
      
# files_csv = ['m0.08',  'm0.125',  'm0.2']
# names = ['r<sub>1</sub>=0.08', 'r<sub>1</sub>=0.125', 'r<sub>1</sub>=0.2' ]
ynames = ['E', 'U<sub>mean</sub>', 'U<sub>max</sub>']#V<sub>g</sub>
fnames = ['Vg', 'Umean', 'Umax']
lines = ['solid', 'dot', 'dash', 'longdash']
print ("path:", rpath)

#WINDOWS 10
path_ex = rpath
#MAC OS
# path_ex = '/Users/weugene/basilisk/work/tube/'
# for i,f in enumerate(files_csv):
#     files_csv[i] = rpath + files_csv[i]
### STYLE
yaxis = dict(
              tickfont = dict(
              family = 'Times New Roman',
              size = 20,
              color = 'black'
              ),
              titlefont = dict(
                  family = 'Times New Roman',
                  size = 25,
                  color = 'black'
              ),
          )
xaxis = dict(
              tickfont = dict(
                  family = 'Times New Roman',
                  size = 20,
                  color = 'black'
              ),
              titlefont = dict(
                  family = 'Times New Roman',
                  size = 25,
                  color = 'black'
              )
          )
# axis_style = dict(showline=True, gridwidth=1, gridcolor='lightgrey', linewidth=2, linecolor='black', mirror=True, ticks='outside',
#                  tickfont = dict(family = 'Times New Roman', size = 18, color = 'black'))
# bg_style = {'plot_bgcolor': 'rgba(255, 255, 255, 1)', 'paper_bgcolor': 'rgba(255, 255, 255, 1)',}
col =   ['blue',           'red',        'hsv(120,100,100)',       'black' ]

### END of STYLE


headers1=['level', 't', 'avggas', 'avggas0', 'avggas_th','statuavg', 'statudev', 'statumin', 'statumax' ]
line_col = {0.05:1, 0.1:2, 0.2:3}
df_exp = []
V0 = []
    
for i, file in enumerate(files_csv):
#     print('FILE name: ',file)
    df_exp.append(pd.read_csv(Path(file), header=None, sep=' '))
    df_exp[i].columns = headers1
    V0.append(df_exp[i]['avggas'][0])
    df_exp[i] = df_exp[i].sample(n=1000).sort_index()
    
    
for j,y in enumerate(['avggas', 'statuavg']):#'statumax'
    fig = go.Figure()
    for i, file in enumerate(files_csv):
        p = params[i]
        r,lev,tol,ir,jlev,ktol = p['r'],p['lev'],p['tol'],p['ir'],p['jlev'],p['ktol']        
        if y =='avggas':
            df_exp[i]['avggas'] = np.abs(df_exp[i]['avggas'] - V0[i])/V0[i]
            
        fig.add_trace(go.Scatter(x=df_exp[i]['t'], y=df_exp[i][y], 
                                 name=names[i],
                                 mode='lines',
                                 line=dict(color=col[ir], width=2, dash = lines[jlev]),
                                 textfont=dict(
                                     family="Times New Roman",
                                     size=18,
                                     color="LightSeaGreen")
                                 ))

    fig.update_layout(
        width = 1000,
        height = 500,
        xaxis_title='t',
        yaxis_title=ynames[j],
        yaxis = yaxis,
        xaxis = xaxis
    )
    fig.update_layout(bg_style)
    fig.update_xaxes(axis_style)
    fig.update_yaxes(axis_style)
    # fig.update_layout( yaxis_type = "log" )
    maxy = max(df_exp[0][y])
    if y == 'statumax':
        maxy = 200
#     fig.update_yaxes(range=[0,0.39])
#     fig.update_xaxes(range=[0,0.39])
    fig.update_layout(showlegend=True)
    fig.update_layout(legend = dict(font = dict(family = "Times New Roman", size = 25, color = "black")),
                      legend_title = dict(font = dict(family = "Times New Roman", size = 25, color = "blue")))

    fig.update_layout(legend=dict(
        yanchor="bottom",
        y=0.1,
        xanchor="left",
        x=1.01,
        bgcolor="White",
        bordercolor="Black",
        borderwidth=figborderlinesize
    ))
    fig.update_layout(
        autosize=False,
        width=850,
        height=600,
        margin=dict(
            l=0,
            r=0,
            b=0,
            t=0,
            pad=0.1
        ),
    #     paper_bgcolor="LightSteelBlue",
    )

    if True:
        fn = rpath + fnames[j] + '.pdf'
        iplot(fig)
        pio.write_image(fig, str(Path(fn)))
        print("Successfully generated:", fn)


path: /home/e.sharaborin/basilisk/work/mass_conservation/logs/


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/logs/Vg.pdf


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/logs/Umean.pdf


# Convergence test for different radii

In [121]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
from plotly.offline import iplot, init_notebook_mode
import plotly.io as pio
import glob, os, sys
import logging
from sys import argv
import re
import csv
from scipy.signal import find_peaks
from pathlib import Path
import os.path

# pio.orca.config.executable = str(Path('C:/Users/Weugene/AppData/Local/Programs/orca/orca.exe'))
np.set_printoptions(threshold=sys.maxsize)
import scipy.spatial.distance as ds

# prefix = 'C:/Users/Weugene/AppData/Local/Packages/CanonicalGroupLimited.UbuntuonWindows_79rhkp1fndgsc/LocalState/rootfs'
prefix = ''
rpath = prefix + '/home/e.sharaborin/basilisk/work/mass_conservation/logs/'

files_csv = []
names = []
params = []
# for r in [0.2]:
#     for lev in [7, 8, 9]:
#         for tol in ['1e-6','1e-8']:
for ir, r in enumerate([0.05, 0.1, 0.2]):
    for jlev, lev in enumerate([7, 8, 9, 10]):
        for ktol, tol in enumerate(['1e-8']):
            file = rpath + 'log_r_{}_l_{}_t_{}'.format(r, lev, tol)
            if os.path.isfile(file) and os.path.getsize(file) > 0:
                files_csv.append(file)
                params.append({'r': r, 'lev': lev, 'tol': tol, 'ir': ir, 'jlev': jlev, 'ktol':ktol})
#                 names.append('r<sub>1</sub>={}, J<sub>max</sub>={}, \u025B<sub>P</sub>={}'.format(r, lev, tol))
#                 names.append('r<sub>1</sub>={}, J<sub>max</sub>={}'.format(r, lev))
                names.append('J<sub>max</sub>={}'.format(lev))
fl = files_csv[:]
      
# files_csv = ['m0.08',  'm0.125',  'm0.2']
# names = ['r<sub>1</sub>=0.08', 'r<sub>1</sub>=0.125', 'r<sub>1</sub>=0.2' ]
ynames = ['E', 'U<sub>mean</sub>', 'U<sub>max</sub>']#V<sub>g</sub>
fnames = ['Vg', 'Umean', 'Umax']
lines = ['longdash', 'dash', 'dot', 'solid']
print ("path:", rpath)

#WINDOWS 10
path_ex = rpath
#MAC OS
# path_ex = '/Users/weugene/basilisk/work/tube/'
# for i,f in enumerate(files_csv):
#     files_csv[i] = rpath + files_csv[i]
### STYLE
yaxis = dict(
              tickfont = dict(
              family = 'Times New Roman',
              size = 20,
              color = 'black'
              ),
              titlefont = dict(
                  family = 'Times New Roman',
                  size = 25,
                  color = 'black'
              ),
          )
xaxis = dict(
              tickfont = dict(
                  family = 'Times New Roman',
                  size = 20,
                  color = 'black'
              ),
              titlefont = dict(
                  family = 'Times New Roman',
                  size = 25,
                  color = 'black'
              )
          )
# axis_style = dict(showline=True, gridwidth=0.5, gridcolor='lightgrey', linewidth=0.5, linecolor='black', mirror=True, ticks='outside',
#                  tickfont = dict(family = 'Times New Roman', size = 18, color = 'black'))
# bg_style = {'plot_bgcolor': 'rgba(255, 255, 255, 1)', 'paper_bgcolor': 'rgba(255, 255, 255, 1)',}
col =   ['blue',           'red',        'hsv(120,100,100)',       'black' ]

### END of STYLE


headers1=['level', 't', 'avggas', 'avggas0', 'avggas_th','statuavg', 'statudev', 'statumin', 'statumax' ]
line_col = {0.05:1, 0.1:2, 0.2:3}
df_exp = []
V0 = []
    
for i, file in enumerate(files_csv):
#     print('FILE name: ',file)
    df_exp.append(pd.read_csv(Path(file), header=None, sep=' '))
    df_exp[i].columns = headers1
    V0.append(df_exp[i]['avggas'][0])
    df_exp[i] = df_exp[i].sample(n=1000).sort_index()
    
r1 = 0.05 # initial radius
tmax = 10000
for j,y in enumerate(['avggas', 'statuavg']):#'statumax'
    fig = go.Figure()
    for i, file in enumerate(files_csv):
        p = params[i]
        r,lev,tol,ir,jlev,ktol = p['r'],p['lev'],p['tol'],p['ir'],p['jlev'],p['ktol']        
        if y =='avggas':
            df_exp[i]['avggas'] = np.abs(df_exp[i]['avggas'] - V0[i])/V0[i]
        
        if r == r1 or i == 0:
            r1 = r
            tmax = min(tmax, df_exp[i]['t'].max())
            fig.add_trace(go.Scatter(x=df_exp[i]['t'], y=df_exp[i][y], 
                                 name=names[i],
                                 mode='lines',
                                 line=dict(color=col[jlev], width=2, dash = lines[jlev]),
                                 textfont=dict(
                                     family="Times New Roman",
                                     size=18,
                                     color="LightSeaGreen")
                                 ))
        if r != r1 or i == len(files_csv) - 1:
            #then save figure and create a new one
            fig.update_layout(
                width = 1000,
                height = 500,
                xaxis_title='t',
                yaxis_title=ynames[j],
                yaxis = yaxis,
                xaxis = xaxis
            )
            fig.update_layout(bg_style)
            fig.update_xaxes(axis_style)
            fig.update_yaxes(axis_style)
            if y == 'avggas':
                fig.update_layout( yaxis_type = "log" )
            maxy = max(df_exp[0][y])
            if y == 'statumax':
                maxy = 200
#             fig.update_yaxes(range=[0,0.39])
            fig.update_xaxes(range=[0,tmax])
            fig.update_layout(showlegend=True, legend_title_text="r<sub>1</sub>="+str(r1))
            fig.update_layout(legend = dict(font = dict(family = "Times New Roman", size = 25, color = "black")),
                              legend_title = dict(font = dict(family = "Times New Roman", size = 25, color = "black")))

            fig.update_layout(legend=dict(
                yanchor="bottom",
                y=0.02,
                xanchor="right",
                x=0.99,
                bgcolor="White",
                bordercolor="Black",
                borderwidth=figborderlinesize
            ))
            fig.update_layout(
                autosize=False,
                width=1000,
                height=500,
                margin=dict(
                    l=0,
                    r=0,
                    b=0,
                    t=0,
                    pad=0.1
                ),
            #     paper_bgcolor="LightSteelBlue",
            )

            if True:
                fn = rpath + fnames[j] + '_r1=' + str(r1) + '.pdf'
                iplot(fig)
                pio.write_image(fig, str(Path(fn)))
                print("Successfully generated:", fn)
            
            # create a new figure:
            r1 = r # discard value
            tmax = 10000 # discard value
            fig = go.Figure(go.Scatter(x=df_exp[i]['t'], y=df_exp[i][y], 
                                 name=names[i],
                                 mode='lines',
                                 line=dict(color=col[jlev], width=2, dash = lines[jlev]),
                                 textfont=dict(
                                     family="Times New Roman",
                                     size=18,
                                     color="LightSeaGreen")
                                 ))
            


path: /home/e.sharaborin/basilisk/work/mass_conservation/logs/


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/logs/Vg_r1=0.05.pdf


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/logs/Vg_r1=0.1.pdf


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/logs/Vg_r1=0.2.pdf


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/logs/Umean_r1=0.05.pdf


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/logs/Umean_r1=0.1.pdf


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/logs/Umean_r1=0.2.pdf


# Converegence for L=10

In [120]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
from plotly.offline import iplot, init_notebook_mode
import plotly.io as pio
import glob, os, sys
import logging
from sys import argv
import re
import csv
from scipy.signal import find_peaks
from pathlib import Path
import os.path

# pio.orca.config.executable = str(Path('C:/Users/Weugene/AppData/Local/Programs/orca/orca.exe'))
np.set_printoptions(threshold=sys.maxsize)
import scipy.spatial.distance as ds

# prefix = 'C:/Users/Weugene/AppData/Local/Packages/CanonicalGroupLimited.UbuntuonWindows_79rhkp1fndgsc/LocalState/rootfs'
prefix = ''
rpath = prefix + '/home/e.sharaborin/basilisk/work/mass_conservation/logs/'
jMAX = 10
files_csv = []
names = []
params = []
# for r in [0.2]:
#     for lev in [7, 8, 9]:
#         for tol in ['1e-6','1e-8']:
for ir, r in enumerate([0.05, 0.1, 0.2]):
    for jlev, lev in enumerate([7, 8, 9, 10]):
        for ktol, tol in enumerate(['1e-8']):
            file = rpath + 'log_r_{}_l_{}_t_{}'.format(r, lev, tol)
            if os.path.isfile(file) and os.path.getsize(file) > 0:
                files_csv.append(file)
                params.append({'r': r, 'lev': lev, 'tol': tol, 'ir': ir, 'jlev': jlev, 'ktol':ktol})
#                 names.append('r<sub>1</sub>={}, J<sub>max</sub>={}, \u025B<sub>P</sub>={}'.format(r, lev, tol))
                names.append('r<sub>1</sub>={}'.format(r))
fl = files_csv[:]
      
# files_csv = ['m0.08',  'm0.125',  'm0.2']
# names = ['r<sub>1</sub>=0.08', 'r<sub>1</sub>=0.125', 'r<sub>1</sub>=0.2' ]
ynames = ['E', 'U<sub>mean</sub>', 'U<sub>max</sub>']#V<sub>g</sub>
fnames = ['Vg', 'Umean', 'Umax']
lines = ['solid', 'dot', 'dash', 'longdash']
print ("path:", rpath)

#WINDOWS 10
path_ex = rpath
#MAC OS
# path_ex = '/Users/weugene/basilisk/work/tube/'
# for i,f in enumerate(files_csv):
#     files_csv[i] = rpath + files_csv[i]
### STYLE
yaxis = dict(
              tickfont = dict(
              family = 'Times New Roman',
              size = 20,
              color = 'black'
              ),
              titlefont = dict(
                  family = 'Times New Roman',
                  size = 25,
                  color = 'black'
              ),
          )
xaxis = dict(
              tickfont = dict(
                  family = 'Times New Roman',
                  size = 20,
                  color = 'black'
              ),
              titlefont = dict(
                  family = 'Times New Roman',
                  size = 25,
                  color = 'black'
              )
          )
# axis_style = dict(showline=True, gridwidth=1, gridcolor='lightgrey', linewidth=2, linecolor='black', mirror=True, ticks='outside',
#                  tickfont = dict(family = 'Times New Roman', size = 18, color = 'black'))
# bg_style = {'plot_bgcolor': 'rgba(255, 255, 255, 1)', 'paper_bgcolor': 'rgba(255, 255, 255, 1)',}
col =   ['blue',           'red',        'hsv(120,100,100)',       'black' ]

### END of STYLE


headers1=['level', 't', 'avggas', 'avggas0', 'avggas_th','statuavg', 'statudev', 'statumin', 'statumax' ]
line_col = {0.05:1, 0.1:2, 0.2:3}
df_exp = []
V0 = []
    
for i, file in enumerate(files_csv):
#     print('FILE name: ',file)
    df_exp.append(pd.read_csv(Path(file), header=None, sep=' '))
    df_exp[i].columns = headers1
    V0.append(df_exp[i]['avggas'][0])
    df_exp[i] = df_exp[i].sample(n=1000).sort_index()
    
tmax = 1e+9    
for j,y in enumerate(['avggas', 'statuavg']):#'statumax'
    fig = go.Figure()
    for i, file in enumerate(files_csv):
        p = params[i]
        r,lev,tol,ir,jlev,ktol = p['r'],p['lev'],p['tol'],p['ir'],p['jlev'],p['ktol']        
        if y =='avggas':
            df_exp[i]['avggas'] = np.abs(df_exp[i]['avggas'] - V0[i])/V0[i]
        tmax = min(tmax, max(df_exp[i]['t']))
        if lev == jMAX:    
            fig.add_trace(go.Scatter(x=df_exp[i]['t'], y=df_exp[i][y], 
                                 name=names[i],
                                 mode='lines',
                                 line=dict(color=col[ir], width=2, dash = lines[ir]),
                                 textfont=dict(
                                     family="Times New Roman",
                                     size=18,
                                     color="LightSeaGreen")
                                 ))

    fig.update_layout(
        width = 1000,
        height = 500,
        xaxis_title='t',
        yaxis_title=ynames[j],
        yaxis = yaxis,
        xaxis = xaxis
    )
    fig.update_layout(bg_style)
    fig.update_xaxes(axis_style)
    fig.update_yaxes(axis_style)
    if y =='avggas':
        fig.update_layout( yaxis_type = "log" )
    maxy = max(df_exp[0][y])
    if y == 'statumax':
        maxy = 200
#     fig.update_yaxes(range=[0,0.39])
    fig.update_xaxes(range=[0,tmax])
    fig.update_layout(showlegend=True, legend_title_text="J<sub>max</sub>="+str(jMAX))
    fig.update_layout(legend = dict(font = dict(family = "Times New Roman", size = 25, color = "black")),
                      legend_title = dict(font = dict(family = "Times New Roman", size = 25, color = "black")))

    fig.update_layout(legend=dict(
        yanchor="bottom",
        y=0.02,
        xanchor="right",
        x=0.99,
        bgcolor="White",
        bordercolor="Black",
        borderwidth=figborderlinesize
    ))
    fig.update_layout(
        autosize=False,
        width=1000,
        height=500,
        margin=dict(
            l=0,
            r=0,
            b=0,
            t=0,
            pad=0.1
        ),
    #     paper_bgcolor="LightSteelBlue",
    )

    if True:
        fn = rpath + fnames[j] + '_maxlev_' + str(jMAX) + '.pdf'
        iplot(fig)
        pio.write_image(fig, str(Path(fn)))
        print("Successfully generated:", fn)


path: /home/e.sharaborin/basilisk/work/mass_conservation/logs/


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/logs/Vg_maxlev_10.pdf


Successfully generated: /home/e.sharaborin/basilisk/work/mass_conservation/logs/Umean_maxlev_10.pdf


In [59]:
files_csv

['/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.05_l_7_t_1e-8',
 '/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.05_l_8_t_1e-8',
 '/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.05_l_9_t_1e-8',
 '/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.05_l_10_t_1e-8',
 '/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.1_l_7_t_1e-8',
 '/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.1_l_8_t_1e-8',
 '/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.1_l_9_t_1e-8',
 '/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.1_l_10_t_1e-8',
 '/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.2_l_7_t_1e-8',
 '/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.2_l_8_t_1e-8',
 '/home/e.sharaborin/basilisk/work/mass_conservation/logs/log_r_0.2_l_9_t_1e-8']

In [47]:
df_exp[0]['t'].max()

9.99399

In [34]:
points = np.array([[0,0],[10,0],[10,10],[0,10]])
x= np.array([0,0.9,0.9,0])
y= np.array([0,0,0.8,0.8])
cnt=np.array([[a,b] for a,b in zip(x,y)])
area = cv2.contourArea(cnt)
print(area) # 100.0
dtype = np.float64

error: OpenCV(4.4.0) /tmp/pip-req-build-99ib2vsi/opencv/modules/imgproc/src/shapedescr.cpp:315: error: (-215:Assertion failed) npoints >= 0 && (depth == CV_32F || depth == CV_32S) in function 'contourArea'


In [35]:
def PolyArea(x,y):
    return 0.5*np.abs(np.dot(x,np.roll(y,1))-np.dot(y,np.roll(x,1)))
PolyArea(x,y)

0.7200000000000001